# Math 124 - Programming for Mathematical Applications
Per-Olof Persson, UC Berkeley

## Homework 8

In [ ]:
# Load the Plots package for all our plotting needs
using Plots

### Assignment Goals

In this homework, we'll build on the `MyPoly` type from our lecture notes. Your task is to extend its functionality by implementing several new methods and features.

A key goal is to practice **generic programming**. As we discussed in class, this means your functions should work correctly for various coefficient types (like `Float64`, `Rational`, or `Complex`). Julia's type system helps a lot, but sometimes you might need functions like `eltype()` or `promote_type()` to get the types just right.

First, let's run the cell below to define the `MyPoly` struct and all the methods we've already created in the lecture.

In [ ]:
# Define a new composite type (struct) for polynomials.
struct MyPoly
    # Field to store coefficients as a vector.
    c::Vector
    # Field for the variable name, e.g., 'x'.
    var::Char
end

# This outer constructor provides a default value for the `var` field.
# It calls the original, inner constructor with 'x' as the second argument.
MyPoly(c) = MyPoly(c, 'x')

# This method of 'degree' is specialized for MyPoly objects.
function degree(p::MyPoly)
    # Find the index of the first non-zero coefficient.
    ix1 = findfirst(p.c .!= 0)
    if ix1 === nothing  # Check if all coefficients are zero.
        return -1
    else
        # The degree is the length of the vector minus the index of the leading term.
        return length(p.c) - ix1
    end
end

# Extend the Base.show function to provide a custom display for MyPoly objects.
function Base.show(io::IO, p::MyPoly)
    d = degree(p)
    print(io, "MyPoly: ")
    if d < 0
        print(io, "0")
        return
    end
    for k = d:-1:0
        coeff = p.c[end-k]
        if coeff == 0 && d > 0
            continue
        end
        if k < d
            if isa(coeff, Real)
                if coeff > 0
                    print(io, " + ")
                else
                    print(io, " - ")
                end
                coeff = abs(coeff)
            else
                print(io, " + ")
            end
        end
        if isa(coeff, Real)
            print(io, coeff)
        else
            print(io, "($coeff)")
        end
        if k == 0
            continue
        end
        print(io, "⋅", p.var)
        if k > 1
            print(io, "^", k)
        end
    end
end

# This method makes MyPoly objects callable.
function (p::MyPoly)(x)
    # Start with the leading coefficient.
    val = p.c[1]
    # Apply Horner's method.
    for i in 2:length(p.c)
        val = val * x + p.c[i]
    end
    return val
end

# Extend Plots.plot! to add a MyPoly to an existing plot.
function Plots.plot!(p::MyPoly; xlim=[-2, 2])
    # Generate a range of x-values for a smooth curve.
    xx = range(xlim[1], xlim[2], length=100)
    # Use broadcasting p.(xx) to evaluate the polynomial at all points.
    plot!(xx, p.(xx), legend=false, grid=true, xlim=xlim)
    xlabel!(string(p.var))
end

# Extend Plots.plot to create a new plot for a MyPoly.
function Plots.plot(p::MyPoly; xlim=[-2, 2])
    # Create a new, empty plot.
    plot()
    # Call our new plot! method to add the polynomial.
    plot!(p; xlim=xlim)
end

# Overload the addition operator for two MyPoly objects.
function Base.:+(p1::MyPoly, p2::MyPoly)
    # Ensure we're not adding polynomials of different variables.
    if p1.var != p2.var
        error("Cannot add polynomials with different independent variables.")
    end

    n1 = length(p1.c)
    n2 = length(p2.c)
    n = max(n1, n2)

    # Pad the shorter coefficient vector with leading zeros.
    c1_padded = [zeros(eltype(p1.c), n - n1); p1.c]
    c2_padded = [zeros(eltype(p2.c), n - n2); p2.c]

    return MyPoly(c1_padded + c2_padded, p1.var)
end

# Overload the subtraction operator.
function Base.:-(p1::MyPoly, p2::MyPoly)
    # Subtraction is the same as adding the negation.
    return p1 + MyPoly(-p2.c, p2.var)
end

# Define scalar multiplication: number * polynomial.
function Base.:*(a, p::MyPoly)
    # Broadcasting the scalar multiplication across the coefficients.
    newc = a * p.c
    return MyPoly(newc, p.var)
end

# Define the reverse order: polynomial * number.
function Base.:*(p::MyPoly, a)
    # Reuse the method we just defined.
    return a * p
end

### Problem 1(a): Polynomial Multiplication

Implement multiplication of two polynomials by overloading the `*` operator (`Base.:*`).

**Hints:**
* The overall structure will be similar to the `+` operator (check for same variable, create new coefficient vector, return new `MyPoly`).
* If $p_1$ has degree $d_1$ and $p_2$ has degree $d_2$, their product $p_1 p_2$ will have degree $d = d_1 + d_2$. The new coefficient vector will need $d+1$ elements.
* Use `promote_type(eltype(p1.c), eltype(p2.c))` to determine the correct element type for the new coefficient vector. This ensures that multiplying an `Int` polynomial by a `Rational` polynomial correctly yields a `Rational` polynomial.

In [ ]:
# Test your function using the code below
println("--- Problem 1(a) Tests ---")
p1 = MyPoly([1,-2])         # x - 2
p2 = MyPoly([4,3,1,1])     # 4x^3 + 3x^2 + x + 1
display(p1 * p2)           # Should be 4x^4 - 5x^3 - 5x^2 - x - 2 (Int coefficients)

p3 = MyPoly([-1//2, 1//3, -1//4]) # (-1/2)x^2 + (1/3)x - 1/4
display(p2 * p3)           # Should have Rational coefficients

### Problem 1(b): Constructor from Roots

Implement a new constructor for the `MyPoly` type that builds a polynomial from a given vector of roots. The resulting polynomial should be **monic** (have a leading coefficient of 1).

For a vector $r = [r_1, r_2, \ldots, r_d]$ with $d$ roots, we want to create the degree $d$ polynomial:

$$ p(x) = (x - r_1)(x - r_2)\cdots(x - r_d) = \prod_{k=1}^d (x - r_k) $$

To avoid conflicting with our existing constructor `MyPoly(c::Vector)`, we'll use a **keyword argument**. This allows for a dispatch mechanism based on the *name* of the argument, not just its type.

Implement the function with this signature:
```julia
function MyPoly(; roots)
    # Your implementation here
end
```
**Hint:** Start with the polynomial $p(x) = 1$ and multiply it by $(x - r_k)$ for each root $r_k$ in the `roots` vector.

In [ ]:
# Test your function using the code below.
println("\n--- Problem 1(b) Tests ---")
    
p_int_roots = MyPoly(roots=[-3,-2,0,1,1,4])
display(p_int_roots)  # Should have integer coefficients

# We'll use this rational polynomial 'p' for the next problems
p = MyPoly(roots=[-7//3,-2//1,0,1//2,1//2,3//2])
display(p)  # Should have rational coefficients

### Problem 1(c): Differentiation

Implement a function `differentiate(p::MyPoly)` which returns the derivative of the polynomial $p$. 

Recall the power rule: $\frac{d}{dx} (c_k x^k) = (k \cdot c_k) x^{k-1}$.

In [ ]:
# Test your function using the code below.
println("\n--- Problem 1(c) Test ---")
display(p) # Original
display(differentiate(p)) # Derivative

### Problem 1(d): Integration

Implement a function `integrate(p::MyPoly)` which returns the (indefinite) integral of $p$. 

Assume the constant of integration is zero (i.e., the constant term of the new polynomial is 0).

Recall the rule: $\int (c_k x^k) dx = \frac{c_k}{k+1} x^{k+1} + C$

In [ ]:
# Test your function using the code below.
println("\n--- Problem 1(d) Test ---")
display(p) # Original
display(integrate(p)) # Integral (should have Rational coefficients)

## Problem 2: Lagrange Polynomials and FEM Matrices

In this problem, we'll use our `MyPoly` type to solve a practical problem from numerical analysis: computing **Lagrange basis polynomials**. 

These polynomials are fundamental to interpolation and are used to build "elemental matrices" in the Finite Element Method (FEM) for solving PDEs.

### Problem 2(a): Lagrange Basis Polynomials

Implement a function `LagrangePolynomials(s)` where `s` is a vector of $n$ numbers (nodes), $s = [s_1, \ldots, s_n]$.

This function should return a vector of $n$ polynomials, $L_k(x)$ (for $k=1,\ldots,n$), each of degree $n-1$. These polynomials must satisfy the *cardinality condition*:

$$ L_k(s_j) = \delta_{kj} = \begin{cases} 1 & \text{if } k=j \\ 0 & \text{if } k \ne j \end{cases} $$

This means $L_k(x)$ is the unique polynomial of degree $n-1$ that is **1** at node $s_k$ and **0** at all other nodes $s_j$ (where $j \ne k$).

**Hint:** Think about the roots! For a specific $L_k(x)$, we know all its roots: they are $s_j$ for all $j \ne k$. 
1.  Use the `MyPoly(roots=...)` constructor from Problem 1(b) to create a polynomial $\ell_k(x)$ that has these $n-1$ roots. 
2.  This polynomial $\ell_k(x)$ is 0 at the correct points, but $\ell_k(s_k)$ is probably not 1. 
3.  Create the final polynomial $L_k(x)$ by scaling $\ell_k(x)$: $L_k(x) = \frac{1}{\ell_k(s_k)} \ell_k(x)$.

In [ ]:
# Test your function using the code below.
println("\n--- Problem 2(a) Test ---")

# Create 7 nodes (degree 6) from 0.0 to 1.0
nodes = (0:6) / 6
Ls_test = LagrangePolynomials(nodes)

# Plot all the Lagrange polynomials on [0, 1]
plot(title="Lagrange Basis Polynomials (Degree 6)", legend=:outertopright, xlim=[0,1])
# We use `plot!.(Ls, ...)` to broadcast the plot! command to each polynomial
plot!.(Ls_test, xlim=[0,1])
plot!()

### Problem 2(b): FEM Mass and Stiffness Matrices

In the Finite Element Method (FEM), two important matrices are the **mass matrix** $M$ and the **stiffness matrix** $K$. For a 1D element on the interval $[0, 1]$ using the Lagrange basis $L_i(x)$, their entries are defined by integrals:

$$ M_{ij} = \int_0^1 L_i(x) L_j(x)\,dx \qquad \text{(Mass Matrix)} $$

$$ K_{ij} = \int_0^1 L_i'(x) L_j'(x)\,dx \qquad \text{(Stiffness Matrix)} $$

where $L_i'(x)$ is the derivative $\frac{dL_i}{dx}$.

Write two functions, `mkM(Ls)` and `mkK(Ls)`, that compute and return these $n \times n$ matrices given a vector `Ls` of $n$ Lagrange polynomials.

**Hint:** To calculate the definite integral $\int_0^1 p(x) dx$ for any polynomial $p$, first find its indefinite integral $P(x) = \int p(x) dx$ (using your `integrate` function). Then, by the Fundamental Theorem of Calculus, the definite integral is $P(1) - P(0)$.

In [ ]:
# Test your functions using the code below.
println("\n--- Problem 2(b) Test ---")

# Set the degree d=4. This means n=d+1=5 nodes.
d = 4

# Create the nodes as *rational* numbers using the `//` operator.
# nodes = [0//1, 1//4, 2//4, 3//4, 4//4]
nodes_rat = (0:d) .// d

# Because the nodes are rational, all subsequent calculations
# (roots, scaling, multiplication, integration) should preserve
# rational arithmetic. The final matrices should be Rational.
Ls_rat = LagrangePolynomials(nodes_rat)
M = mkM(Ls_rat)
K = mkK(Ls_rat)

println("--- Lagrange Polynomials (d=4, Rational) ---")
display(Ls_rat)
println("\n--- Mass Matrix M (Rational) ---")
display(M)
println("\n--- Stiffness Matrix K (Rational) ---")
display(K)